In [ ]:
import agh_db_lectures
agh_db_lectures.prepare_notebook_for_sql()

# Data manipulation in SQL

In [ ]:
agh_db_lectures.download_install_wordpress_site()

## Our site

http://localhost:28080/site

_notes_

So far we've been learning on a toy database.  Now we are going to work with a database schema that is used **a lot** in the wild.

Our demo site is made with Wordpress, one of the most popular (and most often exploited, btw) tools for website creation.

## Wordpress database

In [ ]:
%sql mysql:///agh_it_wordpress?unix_socket=/var/run/mysql/mysql.sock

_notes_

Wordpress famously supports only MySQL (or its fork MariaDB) as its DMBS.  If a WP site is run with another database engine, it is through unofficial forks or plugins.

Note that we are not connecting to the databse over network this time.  We communicate with the DBMS using a special file called "socket".  Both Postgres and MariaDB/MySQL (and also many other DBMSes) allow both network and socket connections.

In [ ]:
%%sql
SHOW TABLES

_notes_

Relational DMBSes typically allow querying the set of tables in the database.

In [ ]:
agh_db_lectures.wp_diagram.download_display()

In [ ]:
agh_db_lectures.wp_diagram.download_open()

_notes_

An entity relationship diagram of the database is additionally available online and we'll use it to our convenience.

## Users table and (not) storing of passwords

In [ ]:
%%sql
select * from wp_users

_notes_

Let's look at the single user row in our site's db.  It contains data of the initial user registered from `agh_db_lectures.py`.

Important digression: note that password is not stored in plaintext on the server.  A password hash is stored instead.  This is is a good security practice.

Upon a login attempt, the provided password is also hashed and the result compared to the hash stored in the db.

Note that this is not the only possible password-based login scheme that avoids storing the password.

In [ ]:
%%sql
SELECT user_login,
       SUBSTR(user_pass, 4, 29) AS salt,
       SUBSTR(user_pass, 33) AS hash
FROM wp_users

_notes_

WP and many other systems store each password hash together with a sequence of bytes called **salt**.  The salt contains some random bytes and is hashed together with the password.  This way, even if the same password is used in multiple systems, hashes stored there shall differ nevertheless.

Note the use of `SUBSTR()` builtin function.  It can be used in the same fashion under Postgres.

In thi case, the salt also includes configuration of the hashing procedure.

- The number of repeated hash function applications (here, 10).
- The cryptographic hash function code (here, `2y`, indicating blowfish cipher).

In [ ]:
import base64
import bcrypt
import hmac
import hashlib

def hash_wp_pwd(pwd, salt):
    pwd_bytes = pwd.encode('utf-8')

    pwd_hmac = hmac.digest(b'wp-sha384', pwd_bytes, 'sha384')
    pwd_hmac_b64 = base64.b64encode(pwd_hmac)

    return bcrypt.hashpw(base64.b64encode(pwd_hmac), salt)

hash_wp_pwd(
    'demo_pwd',
    b'' # Paste salt from the output of the code cell above.
)

_notes_

A Quick example.  The password used by _demo_user_ is "demo_pwd".  We can replicate the hashing procedure of WP in Python.  Note that this example is here for demonstrative purposes, you do not need to understand, e.g., what HMAC is.

## Inserting data into table in SQL

Suppose we want to programatically add a user to the site.

_notes_

Theodore, how do you think, why could we want to write code that adds a user to a Wordpress site?

In [ ]:
def gen_hash_with_salt_for_wp(pwd):
    salt = bcrypt.gensalt(rounds=10).replace(b'$2b', b'$2y')
    
    return b'$wp' + hash_wp_pwd(pwd, salt)

gen_hash_with_salt_for_wp('') # Type a password.

_notes_

Theodore, are you from Cybersecurity or another course?  Theodore please pick a password for your account.

We get salt concatenated with the password hash.  Let's run the code again to simulate another system hashing the same password.  As one can see, the hashes are going to be different.

The basic syntax for adding a row to an SQL table is as follows.

```sql
INSERT INTO table_name
VALUES('column_1_value', 'column_2_value', 'etc.');
```

In [ ]:
%%sql
INSERT INTO wp_users
VALUES(
    2,                             -- ID
    'theodore',                    -- user_login
    -- Paste below the value produced by the code cell above.
    '',
    'Theodore',                    -- user_nicename
    'theo@domain.invalid',         -- user_email
    'http://127.0.0.1:28080/site', -- user_url
    NOW(),                         -- user_registered
    '',                            -- user_activation_key
    0,                             -- user_status
    'Theodore'                     -- display_name
)

_notes_

Please do not feel required to bother yourself with understanding the semantic of each of the columns.

Fill in the hashed password.

The cell below can be used to verify that the row has been added.

Note that we cannot have duplicates in the table, the ID of a user is mandated to be unique.  If we re-run the user creation code without changing the ID, it results in an error.

Note how the correct behavior of the code depends on the order of columns in the table.

Theodore, we'd like to add one more user to the site, in a different way.  Please choose a username for your friend.

We can insert a row while specifying values only for certain columns and allowing the DBMS to use default values for the rest.
Change the `INSERT` line as follows.

```sql
INSERT INTO wp_users(-- ID,
                     -- user_registered,
                     -- user_activation_key,
                     -- user_status,
                     user_url,
                     user_login,
                     user_pass,
                     user_nicename,
                     user_email,
                     display_name)
```

Remove or comment-out the values previously used for `ID`, `user_registered`, `user_activation_key`, and `user_status`.
Adapt the values for `user_login`, `user_pass`, `user_nicename`, `user_email`, and `display_name`.  For `user_pass`, `user_nicename`, and `user_email` you can use the values below.  These will allow logging in with the password "demo_pwd".  Note how double apostrophe can be used in SQL to create a string that itself contains an apostrophe.

```sql
    '$wp$2y$10$GHqeJUGnTkGIVZUFrSRri.P3qpTlpJLWmIFiuH3T76toBn1LN3qaK',
    'Theodore''s Friend',          -- user_nicename
    'friend-of-t@domain.invalid',  -- user_email
```

Look at the inserted row in the output of cell below.  Note how the `ID` column automagically got the next natural number.  It is common to create tables with such automatic id sequences.

Note that the table had no explicitly configured default value for the `user_registered` column.  The implicit default is the `NULL` value.  Note the defaults that were used for the other 2 columns: an empty string and the number 0, respectively.

In [ ]:
%%sql
SELECT * FROM wp_users

Log in at http://127.0.0.1:28080/site/wp-login.php.

_notes_

We can successfully login as one of the new users.  However, we do not have priveleges to do anything on the website.

In [ ]:
%%sql
SELECT * FROM wp_usermeta

_notes_

Some configuration of our users is stored in the `wp_usermeta` table.  Btw, this is a non-relational key-value store implemented on top of a relational database :)

There are quite a few rows corresponding to the initial user.  We could add analogous rows for the other users to grant them admin privileges and other sensible default.

Let's modify this query to return the set of rows that we'd like to see added.

In [ ]:
%%sql
SELECT *
FROM wp_usermeta

_notes_

Firstly, the `session_tokens` key is responsible for current logins.  It'd be better not to include it.  Same with `first_name` and similar keys.  Add the code below.

```sql
WHERE user_id = 1 AND meta_key NOT IN (
    'description',
    'first_name',
    'last_name',
    'nickname',
    'session_tokens'
)
```

Looks good.  We'd now want each of these rows to appear once with `user_id` of 2 and once with `user_id` of 3.

```sql
SELECT umeta_id, id AS user_id, meta_key, meta_value
FROM wp_usermeta CROSS JOIN (SELECT 2 AS id UNION SELECT 3) ids
```

Finally, let's get rid of the `umeta_id` column.

Those are the entries we'd like to be present for our new users.  SQL allows the result of a query to be used in an `INSERT` command in place of the `VALUES` clause.  Add the following in front of the query.

```sql
INSERT INTO wp_usermeta(user_id, meta_key, meta_value)
```

Theodore, is it clear what we are trying to achieve here?

Let's check the result in the code cell above (optionally adding `WHERE meta_key <> 'session_tokens'` to make the table narrower and thus more readable).  Then, try to log in again as Theodore or Theodore's friend.

### The "RETURNING" keyword

In [ ]:
%%sql
INSERT INTO wp_usermeta(user_id, meta_key, meta_value)
VALUES(3, 'last_name', '') -- Fill in the last name.
RETURNING umeta_id

_notes_

It is convenient to have the database choose an id for the new row and return its value from the `INSERT` query.  The `RETURNING` keyword can be used for this.

`RETURNING` is nonstandard but supported by several highly popular database engines.

We shall add 1 more row to `wp_usermeta` to demonstrate this.  Theodore, what is your friend's surname?

Fill in the surname and run the query.

## Modifying existing rows

Let's write a new post on the website, then log out and add an anonymous comment or 2 under it.

_notes_

When we make a comment, it is not displayed automatically.  Approval of a moderator is needed.  Let's look into the `wp_comments` table and see how this is implemented.

In [ ]:
%%sql
SELECT *
FROM wp_comments

_notes_

The `comment_approved` column appears relevant.  It holds value 1 for approved comments and value 0 for unapproved ones.

Note that MySQL/MariaDB lacks a true `BOOLEAN` type.  Instead, wherever a programmer tries to use the `BOOLEAN` type, a small integer type is used instead.  Try with `SELECT TRUE;`.

The SQL syntax for changing rows is as below.

```sql
UPDATE table_name
SET column_1 = 'value 1',
    column_2 = 'value 2'
    -- , etc.
WHERE some_condition
```

In [ ]:
%%sql
UPDATE -- Fill in.
SET -- Fill in.
WHERE -- Fill in.

_notes_

Theodore, for which comment do we want to set `comment_approved` to 1?  Maybe both?

Theodore, what do you wish to use in the `WHERE` condition?  The comment id or its author's name or email?  Or maybe sth else?

Craft a command like below.

```sql
UPDATE wp_comments
SET comment_approved = 1
WHERE comment_id = 3
```

The respective row now has value 1 in that column and the comment is displayed to visitors.  Theodore, is this what we wanted?

Of course an attempt to put an invalid value in a row will result in an error.  Try, for example, the code below.

```sql
UPDATE wp_comments
SET comment_id = 1
WHERE comment_id <> 1
```

## Removing rows

We can use a plugin like Fakerpress to generate a lot of spammy posts and comments on our site.

_notes_

It needs to be first activated from WP dashboard.  About ~20  generated posts and ~100 comments should be enough for our experiments.

In [ ]:
%%sql
SELECT ID, post_date, post_title FROM wp_posts

The syntax for row deletion from SQL table is as follows.

```sql
DELETE FROM table_name
WHERE some_codition
```

In [ ]:
%%sql
DELETE FROM -- fill in
WHERE -- fill in

_notes_

Theodore, what attribute of `wp_posts` would you like to use in our SQL command to determine which rows to remove?  `ID`, `post_date`?  Or maybe sth else?

Run a command like below.
```sql
DELETE FROM wp_posts
WHERE ID > 5
```

Note that data manipulation commands (not just `DELETE`, even though we mention this here) can also utilize subqueries.  E.g. `WHERE ID > (SELECT 5)` would work just as well in this case.

Note that MariaDB and Postgres also support `RETURNING` with `DELETE`.

```sql
DELETE FROM wp_comments
WHERE comment_id > 3
RETURNING comment_id, comment_post_id
```

## The "UPSERT" functionality

E.g., try to insert row(s), but update them instead if already present.

In [ ]:
%%sql
INSERT INTO wp_users
VALUES(
    10000001,                      -- ID
    'wp_bot',                      -- user_login
    '$wp$2y$10$GHqeJUGnTkGIVZUFrSRri.P3qpTlpJLWmIFiuH3T76toBn1LN3qaK',
    'Bot',                         -- user_nicename
    'bot@domain.invalid',          -- user_email
    'http://127.0.0.1:28080/site', -- user_url
    NOW(),                         -- user_registered
    '',                            -- user_activation_key
    0,                             -- user_status
    'Bot'                          -- display_name
)
ON DUPLICATE KEY UPDATE
    user_login = 'wp_bot',
    user_pass = '$wp$2y$10$GHqeJUGnTkGIVZUFrSRri.P3qpTlpJLWmIFiuH3T76toBn1LN3qaK',
    user_nicename = 'Bot',
    user_email = 'bot@domain.invalid',
    user_url = 'http://127.0.0.1:28080/site',
    user_registered = NOW(),
    user_activation_key = '',
    user_status = 0,
    display_name = 'Bot'

_notes_

Theodore, is it clear what this command does?

This `UPSERT` functionlity does not belong to standard SQL.  Postgres supports something analogous with slightly different syntax.  Here we used these words.

```sql
ON DUPLICATE KEY UPDATE
```
Under Postgres we would instead write.

```sql
ON CONFLICT DO UPDATE SET
```

Despite the frequently used name of this functionality, no language keyword `UPSERT` is used here, under either DMBS.

### Idempotency

From [Wikipedia](https://en.wikipedia.org/wiki/Idempotence).

> Idempotence is the property of certain operations in mathematics and computer science whereby they can be applied multiple times without changing the result beyond the initial application.

_notes_

Our `UPSERT` command can be executed multiple times.  Subsequent executions do not further change the state.  We can thus call the command we wrote **idempotent**.

A plain `INSERT` would not be idempotent… unless its subsequent executions were to fail with error due to key conflict.